##### Copyright 2021 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# 단일 작업자 멀티 GPU 훈련 마이그레이션하기

<table class="tfo-notebook-buttons" align="left">
  <td><a target="_blank" href="https://www.tensorflow.org/guide/migrate/mirrored_strategy"><img src="https://www.tensorflow.org/images/tf_logo_32px.png">TensorFlow.org에서 보기</a></td>
  <td>     <a target="_blank" href="https://colab.research.google.com/github/tensorflow/docs-l10n/blob/master/site/ko/guide/migrate/mirrored_strategy.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png">Google Colab에서 실행하기</a>
</td>
  <td><a target="_blank" href="https://github.com/tensorflow/docs-l10n/blob/master/site/ko/guide/migrate/mirrored_strategy.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png">GitHub에서 소스 보기</a></td>
  <td>     <a href="https://storage.googleapis.com/tensorflow_docs/docs-l10n/site/ko/guide/migrate/mirrored_strategy.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png">노트북 다운로드하기</a>   </td>
</table>

이 가이드는 단일 작업자 멀티 GPU 워크플로를 TensorFlow 1에서 TensorFlow 2로 마이그레이션하는 방법을 설명합니다.

다음과 같이 한 머신에서 멀티 GPU로 동기식 훈련을 수행할 수 있습니다.

- TensorFlow 1에서는 `tf.distribute.MirroredStrategy`와 함께 `tf.estimator.Estimator` API를 사용합니다.
- TensorFlow 2에서는 `tf.distribute.MirroredStrategy`와 함께 [Keras Model.fit](https://www.tensorflow.org/tutorials/distribute/keras) 또는 [사용자 정의 훈련 루프](https://www.tensorflow.org/tutorials/distribute/custom_training)를 사용할 수 있습니다. [TensorFlow를 사용하는 분산 훈련](https://www.tensorflow.org/guide/distributed_training#mirroredstrategy) 가이드에서 자세히 알아보세요.

## 설치하기

데모를 위해 가져오기 및 간단한 데이터세트로 시작해 보겠습니다.

In [2]:
import tensorflow as tf
import tensorflow.compat.v1 as tf1

2022-12-14 20:56:33.665268: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2022-12-14 20:56:33.665362: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2022-12-14 20:56:33.665372: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


In [3]:
features = [[1., 1.5], [2., 2.5], [3., 3.5]]
labels = [[0.3], [0.5], [0.7]]
eval_features = [[4., 4.5], [5., 5.5], [6., 6.5]]
eval_labels = [[0.8], [0.9], [1.]]

## TensorFlow 1: tf.estimator.Estimator로 단일 작업자 분산 훈련하기

이 예제는 단일 작업자 멀티 GPU 훈련의 TensorFlow 1 정식 워크플로를 보여줍니다. `tf.estimator.Estimator`의 `config` 매개변수를 통해 배포 전략(`tf.distribute.MirroredStrategy`)을 설정해야 합니다.

In [4]:
def _input_fn():
  return tf1.data.Dataset.from_tensor_slices((features, labels)).batch(1)

def _eval_input_fn():
  return tf1.data.Dataset.from_tensor_slices(
      (eval_features, eval_labels)).batch(1)

def _model_fn(features, labels, mode):
  logits = tf1.layers.Dense(1)(features)
  loss = tf1.losses.mean_squared_error(labels=labels, predictions=logits)
  optimizer = tf1.train.AdagradOptimizer(0.05)
  train_op = optimizer.minimize(loss, global_step=tf1.train.get_global_step())
  return tf1.estimator.EstimatorSpec(mode, loss=loss, train_op=train_op)

strategy = tf1.distribute.MirroredStrategy()
config = tf1.estimator.RunConfig(
    train_distribute=strategy, eval_distribute=strategy)
estimator = tf1.estimator.Estimator(model_fn=_model_fn, config=config)

train_spec = tf1.estimator.TrainSpec(input_fn=_input_fn)
eval_spec = tf1.estimator.EvalSpec(input_fn=_eval_input_fn)
tf1.estimator.train_and_evaluate(estimator, train_spec, eval_spec)

INFO:tensorflow:Using MirroredStrategy with devices ('/job:localhost/replica:0/task:0/device:GPU:0', '/job:localhost/replica:0/task:0/device:GPU:1', '/job:localhost/replica:0/task:0/device:GPU:2', '/job:localhost/replica:0/task:0/device:GPU:3')


INFO:tensorflow:Initializing RunConfig with distribution strategies.


INFO:tensorflow:Not using Distribute Coordinator.


INFO:tensorflow:Using config: {'_model_dir': '/tmpfs/tmp/tmpsa7ofgbq', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': <tensorflow.python.distribute.mirrored_strategy.MirroredStrategyV1 object at 0x7f71cc39a4f0>, '_device_fn': None, '_protocol': None, '_eval_distribute': <tensorflow.python.distribute.mirrored_strategy.MirroredStrategyV1 object at 0x7f71cc39a4f0>, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_session_creation_timeout_secs': 7200, '_checkpoint_save_graph_def': True, '_service': None, '_cluster_spec': ClusterSpec({}), '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_c

INFO:tensorflow:Not using Distribute Coordinator.


...

INFO:tensorflow:Saving dict for global step 0: global_step = 0, loss = 4.14284


2022-12-14 20:56:42.774847: W tensorflow/core/grappler/utils/graph_view.cc:836] No registered 'MultiDeviceIteratorFromStringHandle' OpKernel for GPU devices compatible with node {{node MultiDeviceIteratorFromStringHandle}}
	.  Registered:  device='CPU'

2022-12-14 20:56:42.776096: W tensorflow/core/grappler/utils/graph_view.cc:836] No registered 'MultiDeviceIteratorGetNextFromShard' OpKernel for GPU devices compatible with node {{node MultiDeviceIteratorGetNextFromShard}}
	.  Registered:  device='CPU'

2022-12-14 20:56:42.779027: W tensorflow/core/grappler/utils/graph_view.cc:836] No registered 'MultiDeviceIteratorFromStringHandle' OpKernel for GPU devices compatible with node {{node MultiDeviceIteratorFromStringHandle}}
	.  Registered:  device='CPU'

2022-12-14 20:56:42.779503: W tensorflow/core/grappler/utils/graph_view.cc:836] No registered 'MultiDeviceIteratorGetNextFromShard' OpKernel for GPU devices compatible with node {{node MultiDeviceIteratorGetNextFromShard}}
	.  Registered:

INFO:tensorflow:Saving 'checkpoint_path' summary for global step 0: /tmpfs/tmp/tmpsa7ofgbq/model.ckpt-0


INFO:tensorflow:Loss for final step: None.


({'loss': 4.14284, 'global_step': 0}, [])

## TensorFlow 2: Keras로 단일 작업자 훈련하기

TensorFlow 2로 마이그레이션하는 경우 `tf.distribute.MirroredStrategy`와 함께 Keras API를 사용할 수 있습니다.

모델 빌드에 `tf.keras` API를 사용하고 훈련에 Keras `Model.fit`을 사용하는 경우 주요 차이점은 `tf.estimator.Estimator`에 `config`를 정의하는 대신 `Strategy.scope` 컨텍스트에서 Keras 모델, 옵티마이저 및 메트릭을 인스턴스화하는 것입니다.

사용자 정의 훈련 루프를 사용해야 하는 경우 [사용자 정의 훈련 루프와 함께 tf.distribute.Strategy 사용하기](https://www.tensorflow.org/guide/distributed_training#using_tfdistributestrategy_with_custom_training_loops) 가이드를 확인하세요.

In [5]:
dataset = tf.data.Dataset.from_tensor_slices((features, labels)).batch(1)
eval_dataset = tf.data.Dataset.from_tensor_slices(
      (eval_features, eval_labels)).batch(1)

In [6]:
strategy = tf.distribute.MirroredStrategy()
with strategy.scope():
  model = tf.keras.models.Sequential([tf.keras.layers.Dense(1)])
  optimizer = tf.keras.optimizers.Adagrad(learning_rate=0.05)

model.compile(optimizer=optimizer, loss='mse')
model.fit(dataset)
model.evaluate(eval_dataset, return_dict=True)

INFO:tensorflow:Using MirroredStrategy with devices ('/job:localhost/replica:0/task:0/device:GPU:0', '/job:localhost/replica:0/task:0/device:GPU:1', '/job:localhost/replica:0/task:0/device:GPU:2', '/job:localhost/replica:0/task:0/device:GPU:3')


INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).


INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).


INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).


INFO:tensorflow:Reduce to /job:localhost/replica:0/task:0/device:CPU:0 then broadcast to ('/job:localhost/replica:0/task:0/device:CPU:0',).


...

3/3 [==============================] - 4s 8ms/step - loss: 10.0149


2022-12-14 20:56:47.563081: W tensorflow/core/grappler/optimizers/data/auto_shard.cc:784] AUTO sharding policy will apply DATA sharding policy as it failed to apply FILE sharding policy because of the following reason: Found an unshardable source dataset: name: "TensorSliceDataset/_2"
op: "TensorSliceDataset"
input: "Placeholder/_0"
input: "Placeholder/_1"
attr {
  key: "Toutput_types"
  value {
    list {
      type: DT_FLOAT
      type: DT_FLOAT
    }
  }
}
attr {
  key: "_cardinality"
  value {
    i: 3
  }
}
attr {
  key: "is_files"
  value {
    b: false
  }
}
attr {
  key: "metadata"
  value {
    s: "\n\025TensorSliceDataset:26"
  }
}
attr {
  key: "output_shapes"
  value {
    list {
      shape {
        dim {
          size: 2
        }
      }
      shape {
        dim {
          size: 1
        }
      }
    }
  }
}
attr {
  key: "replicate_on_split"
  value {
    b: false
  }
}
experimental_type {
  type_id: TFT_PRODUCT
  args {
    type_id: TFT_DATASET
    args {
      t

1/3 [=========>....................] - ETA: 3s - loss: 26.8715

3/3 [==============================] - 2s 6ms/step - loss: 43.8888


{'loss': 43.888824462890625}

## 다음 단계

TensorFlow 2에서 `tf.distribute.MirroredStrategy`를 사용하는 분산 훈련에 대한 자세한 내용은 다음 문서를 확인하세요

- [Keras를 사용하여 하나의 머신에서 분산 훈련하기](../../tutorials/distribute/keras) 튜토리얼
- [사용자 정의 훈련 루프로 하나의 머신에서 분산 훈련하기](../../tutorials/distribute/custom_training) 튜토리얼
- [TensorFlow를 사용하여 분산 훈련하기](../../guide/distributed_training) 가이드
- [멀티 GPU 사용하기](../../guide/gpu#using_multiple_gpus) 가이드
- [멀티 GPU 단일 호스트에서 성능 최적화하기(TensorFlow 프로파일러 사용)](../../guide/gpu_performance_analysis#2_optimize_the_performance_on_the_multi-gpu_single_host) 가이드